In [1]:
import itertools
import numpy as np
import pandas as pd
from sklearn.preprocessing import LabelEncoder

In [2]:
papers = pd.read_csv('dblp.v12.csv')
papers['authors'] = papers['authors'].apply(eval)
papers['references'] = papers['references'].apply(eval)
papers['fos'] = papers['fos'].apply(eval)
print(papers.shape)
papers.head()

(1002355, 8)


id                                              title  \
0   1091  Preliminary Design of a Network Protocol Learn...   
1  15883  Leveraging legacy code to deploy desktop appli...   
2  15901  A pedestrian navigation method for user's safe...   
3  38917  Automated Object Identification and Position E...   
4  58261   A general semantic analyser for data base access   

                                            abstract  year  label  \
0  The purpose of this study is to develop a lear...  2013      6   
1  Xax is a browser plugin model that enables dev...  2008      4   
2  In recent years, most of mobile phones have a ...  2013      6   
3  The development of an automated system for the...  2008      0   
4  The paper discusses the design principles and ...  1981      0   

                                             authors  \
0  [2312688602, 2482909946, 2128134587, 210178269...   
1    [135218249, 2120803867, 2128381254, 2150137935]   
2                           [2789599552, 2935910818]   
3   [2068146743, 2252543171, 1278895136, 2171534607]   
4                           [2316496857, 2169254595]   

                                          references  \
0                           [2005687710, 2018037215]   
1  [114793137, 186343359, 205258527, 1516211918, ...   
2               [2055819696, 2167564737, 2169528473]   
3  [96589161, 2138661420, 2157641950, 2163004336,...   
4   [1997320166, 2042008249, 2043794661, 2061141062]   

                                                 fos  
0  [telecommunications network, computer science,...  
1  [world wide web, computer science, machine cod...  
2  [visibility, route planning, computer science,...  
3  [computer vision, aerodrome, image sensor, com...  
4  [front and back ends, design elements and prin...

In [3]:
# Extend the `references` column to a List[2005687710, 2018037215, 114793137, ...]
all_references = np.array(list(itertools.chain(*(papers['references'].values))))

# Construct a list containing the `id` corresponding to the above references list
paper_ids = np.concatenate([np.full(count, i) 
                                 for i, count in zip(papers['id'].values, papers['references'].apply(len))])

assert len(all_references) == len(paper_ids)

# Wether a reference is in the `id` column
in_paperids = np.isin(all_references, papers['id'].values)
len(in_paperids), in_paperids.sum() 

(14072159, np.int64(7876504))

In [4]:
# Filter the references list
all_references = all_references[in_paperids]
paper_ids = paper_ids[in_paperids]

In [5]:
has_reference1 = np.isin(papers['id'].values, paper_ids)
has_reference2 = np.isin(papers['id'].values, all_references)
has_reference = has_reference1 | has_reference2
papers = papers[has_reference]
print('Number of papers that refer or are referred', papers.shape[0])
papers.head()

Number of papers that refer or are referred 964350


id                                              title  \
1  15883  Leveraging legacy code to deploy desktop appli...   
2  15901  A pedestrian navigation method for user's safe...   
3  38917  Automated Object Identification and Position E...   
4  58261   A general semantic analyser for data base access   
5  65220  Two notes from experimental study on image ste...   

                                            abstract  year  label  \
1  Xax is a browser plugin model that enables dev...  2008      4   
2  In recent years, most of mobile phones have a ...  2013      6   
3  The development of an automated system for the...  2008      0   
4  The paper discusses the design principles and ...  1981      0   
5  In recent years, several advanced methods for ...  2013      0   

                                            authors  \
1   [135218249, 2120803867, 2128381254, 2150137935]   
2                          [2789599552, 2935910818]   
3  [2068146743, 2252543171, 1278895136, 2171534607]   
4                          [2316496857, 2169254595]   
5              [2304723528, 2676058149, 2120394816]   

                                          references  \
1  [114793137, 186343359, 205258527, 1516211918, ...   
2               [2055819696, 2167564737, 2169528473]   
3  [96589161, 2138661420, 2157641950, 2163004336,...   
4   [1997320166, 2042008249, 2043794661, 2061141062]   
5  [22271197, 29798142, 1713630528, 1955882805, 2...   

                                                 fos  
1  [world wide web, computer science, machine cod...  
2  [visibility, route planning, computer science,...  
3  [computer vision, aerodrome, image sensor, com...  
4  [front and back ends, design elements and prin...  
5  [steganography, steganography tools, pattern r...

## Paper-Paper Links

In [6]:
data = {}

In [7]:
paper_id_encoder = LabelEncoder()
paper_id_encoder.fit(papers['id'].values)
all_references = paper_id_encoder.transform(all_references).astype(np.int32)
paper_ids = paper_id_encoder.transform(paper_ids).astype(np.int32)

In [8]:
src = np.concatenate((paper_ids, all_references))
dst = np.concatenate((all_references, paper_ids))
mask = src < dst
src = src[mask]
dst = dst[mask]

print('Number of paper-paper links:', src.shape[0])
data['paper-paper'] = (src, dst)

Number of paper-paper links: 7876504


## Paper-Author Links

In [9]:
paper_ids = np.concatenate([np.full(count, i) 
                                 for i, count in zip(papers['id'].values, papers['authors'].apply(len))])
authors = list(itertools.chain(*(papers['authors'].values)))

In [10]:
author_id_encoder = LabelEncoder()
author_ids = author_id_encoder.fit_transform(authors).astype(np.int32)
print('Number of authors:', len(author_id_encoder.classes_))

Number of authors: 958961


In [11]:
paper_ids = paper_id_encoder.transform(paper_ids).astype(np.int32)
assert len(author_ids) == len(paper_ids)
print('Number of paper-author links:', paper_ids.shape[0])
data['paper-author'] = (paper_ids, author_ids)

Number of paper-author links: 3070343


## Paper-FoS Links

In [12]:
paper_ids = np.concatenate([np.full(count, i) 
                                 for i, count in zip(papers['id'].values, papers['fos'].apply(len))])
foss = list(itertools.chain(*(papers['fos'].values)))

In [13]:
fos_id_encoder = LabelEncoder()
fos_ids = fos_id_encoder.fit_transform(foss).astype(np.int32)
print('Number of FoS:', len(fos_id_encoder.classes_))

Number of FoS: 65699


In [14]:
paper_ids = paper_id_encoder.transform(paper_ids).astype(np.int32)

assert len(fos_ids) == len(paper_ids)
print('Number of paper-fos links:', fos_ids.shape[0])
data['paper-fos'] = (paper_ids, fos_ids)

Number of paper-fos links: 10086883


## Labels and Years

In [15]:
# Reorder papers

papers.set_index('id', inplace=True)
papers = papers.loc[paper_id_encoder.classes_]
papers.reset_index(inplace=True)
papers.tail()


id                                              title  \
964345  3008425973  A Simulation Model Demonstrating the Impact of...   
964346  3008480875  Scaling Blockchains to Support Electronic Heal...   
964347  3008559546       How Good Is a Strategy in a Game with Nature   
964348  3008721399  Chunking in Soar: The Anatomy of a General Lea...   
964349  3008773848  Shorter identifier names take longer to compre...   

                                                 abstract  year  label  \
964345  In addition to seamless connectivity and smart...  2020      0   
964346  Electronic Health Records (EHRs) have improved...  2020      2   
964347  We consider games with two antagonistic player...  2020      7   
964348  In this article we describe an approach to the...  1986      0   
964349  Developers spend the majority of their time co...  2017      4   

                                     authors  \
964345                          [3008013535]   
964346  [3000482756, 2560842277, 2096420846]   
964347              [2083017933, 2033699461]   
964348   [2098086841, 237745248, 2126658068]   
964349  [2576839772, 2145688174, 2166709612]   

                                               references  \
964345  [1969595988, 2024456547, 2106660896, 240927666...   
964346  [1593596963, 2038708100, 2071551483, 216457208...   
964347  [157185084, 744920664, 1502459210, 1513485037,...   
964348  [10646503, 38913427, 86408651, 152570004, 1597...   
964349  [1490674333, 1842503650, 1967931023, 203468809...   

                                                      fos  
964345  [social objects, computer science, cooperative...  
964346  [health care, architecture, computer science, ...  
964347  [discrete mathematics, graph, infinite game, d...  
964348  [anatomy, architecture, chunking (psychology),...  
964349  [identifier, computer science, artificial inte...

In [16]:
paper_years = papers['year'].values.astype(np.int16)
data['paper_years'] = paper_years

In [17]:
paper_labels = papers['label'].values.astype(np.int8)
data['paper_labels'] = paper_labels

In [18]:
data

{'paper-paper': (array([    0,     0,     0, ..., 16345,   732,  7251], dtype=int32),
  array([13858, 61018, 81249, ..., 19830,   744, 19890], dtype=int32)),
 'paper-author': (array([    0,     0,     0, ..., 19890, 19890, 19882], dtype=int32),
  array([ 10439, 196586, 212053, ..., 685977, 455354, 510243], dtype=int32)),
 'paper-fos': (array([    0,     0,     0, ..., 19882, 19882, 19882], dtype=int32),
  array([65253, 10791, 33819, ..., 43792,  2953, 38524], dtype=int32)),
 'paper_years': array([2008, 2013, 2008, ..., 2020, 1986, 2017], dtype=int16),
 'paper_labels': array([4, 6, 0, ..., 7, 0, 4], dtype=int8)}

In [19]:
papers.to_csv('DBLP.csv', index=False)

### Node Features

We generate embeddings as features for each node in the graph. Node embeddings are generated by passing the title and the abstract through a Sentence-BERT model and obtaining a 384-embedding vector for each movie node.


According to [Sentence-Transformers docs](https://www.sbert.net/docs/pretrained_models.html), the **all-MiniLM-L6-v2** model provides the best quality. So we use it to generate node features.

all-MiniLM-L6-v2

Description:	All-round model tuned for many use-cases. Trained on a large and diverse dataset of over 1 billion training pairs.
Base Model:	nreimers/MiniLM-L6-H384-uncased
Max Sequence Length:	256
Dimensions:	384
Normalized Embeddings:	true
Suitable Score Functions:	dot-product (util.dot_score), cosine-similarity (util.cos_sim), euclidean distance
Size:	80 MB
Pooling:	Mean Pooling
Training Data:	1B+ training pairs. For details, see model card.
Model Card:	https://huggingface.co/sentence-transformers/all-MiniLM-L6-v2


In [20]:
import torch
from sentence_transformers import SentenceTransformer

device = 'cuda:0' if torch.cuda.is_available() else 'cpu'
model = SentenceTransformer('../sentence-transformers/all-MiniLM-L6-v2', device=device)
model

/usr/local/lib/python3.10/dist-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


SentenceTransformer(
  (0): Transformer({'max_seq_length': 256, 'do_lower_case': False}) with Transformer model: BertModel 
  (1): Pooling({'word_embedding_dimension': 384, 'pooling_mode_cls_token': False, 'pooling_mode_mean_tokens': True, 'pooling_mode_max_tokens': False, 'pooling_mode_mean_sqrt_len_tokens': False, 'pooling_mode_weightedmean_tokens': False, 'pooling_mode_lasttoken': False, 'include_prompt': True})
  (2): Normalize()
)

In [21]:
text = papers['title'] + ' ' + papers['abstract']

In [22]:
feats = model.encode(text, batch_size=4096, show_progress_bar=True, convert_to_numpy=True)

Batches: 100%|██████████| 236/236 [12:22<00:00,  3.15s/it]


In [23]:
data['paper_feats'] = feats
data

{'paper-paper': (array([    0,     0,     0, ..., 16345,   732,  7251], dtype=int32),
  array([13858, 61018, 81249, ..., 19830,   744, 19890], dtype=int32)),
 'paper-author': (array([    0,     0,     0, ..., 19890, 19890, 19882], dtype=int32),
  array([ 10439, 196586, 212053, ..., 685977, 455354, 510243], dtype=int32)),
 'paper-fos': (array([    0,     0,     0, ..., 19882, 19882, 19882], dtype=int32),
  array([65253, 10791, 33819, ..., 43792,  2953, 38524], dtype=int32)),
 'paper_years': array([2008, 2013, 2008, ..., 2020, 1986, 2017], dtype=int16),
 'paper_labels': array([4, 6, 0, ..., 7, 0, 4], dtype=int8),
 'paper_feats': array([[-0.09045218, -0.04914903, -0.00183934, ..., -0.02621997,
          0.10682236,  0.03757928],
        [ 0.05457439, -0.03537758, -0.00981656, ...,  0.02816821,
         -0.08244677,  0.05598091],
        [ 0.05163385, -0.00435178,  0.00543169, ...,  0.04312224,
         -0.08650234,  0.02618632],
        ...,
        [ 0.00644145, -0.02942889, -0.03935754,

In [24]:
import pickle

with open('dblp.pkl', 'wb') as f:
    pickle.dump(data, f)